In [1]:
#Deps
import os
import numpy as np
import matplotlib.pyplot as plt
import librosa
import librosa.display
from IPython.display import display, Audio
from asteroid.models import BaseModel
import soundfile as sf
from julius import ResampleFrac
import speech_recognition as sr
from pydub import AudioSegment

C:\Users\jogit\anaconda3\envs\ir\lib\site-packages\pydub\utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
  warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)


In [2]:
#audio source paths
source_path = "C:/Users/jogit/Documents/IR repos/CSE508_Winter2023_Group2_Project/model-testing/female-female-mixture.wav"
source_path2 = "C:/Users/jogit/Documents/IR repos/CSE508_Winter2023_Group2_Project/model-testing/female-male-mixture.wav"

In [3]:
#Check audio loading
display(Audio(source_path))
display(Audio(source_path2))

In [4]:
#Load model using asteroid
model = BaseModel.from_pretrained("mpariente/ConvTasNet_WHAM_sepclean")

In [5]:
#load audio and convert to input format for audio 1
base_audio, sample_rate = sf.read(source_path, dtype="float32", always_2d=True)
#convert shape to (batch, channels, time)
mixture = base_audio.transpose()
mixture = mixture.reshape(1, mixture.shape[0], mixture.shape[1])
print(mixture.shape)
output = model.separate(mixture)
print(output.shape)

(1, 1, 84318)
(1, 2, 84318)


In [6]:
#convert numpy array to wav file
save_name_template = os.path.basename(source_path)[:-4] + "_est{}.wav"

separated_output = [output[0,i,:] for i in range(output.shape[1])]

for src_idx, est_src in enumerate(separated_output, 1):
        sf.write(save_name_template.format(src_idx), est_src, sample_rate)
        
#display separated audio
for src_idx, est_src in enumerate(separated_output, 1):
    display(Audio(save_name_template.format(src_idx)))

In [7]:
sound = AudioSegment.from_file(source_path2, format="wav")

# Convert to mono
sound = sound.set_channels(1)

# Export as a mono audio file
path_parts = source_path2.split(os.path.sep)[:-1]
source_path2 = os.path.join(os.path.sep.join(path_parts), "mono_audio.wav")
sound.export(source_path2, format="wav")

<_io.BufferedRandom name='mono_audio.wav'>

In [8]:
#load audio and convert to input format for audio 1
base_audio, sample_rate = sf.read(source_path2, dtype="float32", always_2d=True)
#convert shape to (batch, channels, time)
mixture = base_audio.transpose()
mixture = mixture.reshape(1, mixture.shape[0], mixture.shape[1])
print(mixture.shape)
output = model.separate(mixture)
print(output.shape)

(1, 1, 683136)
(1, 2, 683136)


In [9]:
#convert numpy array to wav file
save_name_template2 = os.path.basename(source_path2)[:-4] + "_est{}.wav"

separated_output = [output[0,i,:] for i in range(output.shape[1])]

for src_idx, est_src in enumerate(separated_output, 1):
        sf.write(save_name_template2.format(src_idx), est_src, sample_rate)
        
#display separated audio
for src_idx, est_src in enumerate(separated_output, 1):
    display(Audio(save_name_template2.format(src_idx)))

In [11]:
r = sr.Recognizer()

with sr.AudioFile("single-source-transcribe.wav") as source:
    audio_data = r.record(source)
    text = r.recognize_google(audio_data)
print(text)

result2:
{   'alternative': [   {   'confidence': 0.88430041,
                           'transcript': 'wetron actress Satish Kaushik passed '
                                         'away on March 9 2023 the senior '
                                         'actors suffered a heart attack while '
                                         'he was travelling in a car in Delhi '
                                         'his sudden demise left everyone '
                                         'Satin the film industry is still '
                                         'unable to come to terms with his '
                                         'loss'},
                       {   'transcript': 'wetron actress Satish Kaushik passed '
                                         'away on March 9 2023 the senior '
                                         'actor suffered a heart attack while '
                                         'he was travelling in a car in Delhi '
                       

In [ ]:
for src_idx, est_src in enumerate(separated_output, 1):
    with sr.AudioFile(save_name_template.format(src_idx)) as source:
        audio_data = r.record(source)
        text = r.recognize_google(audio_data)
    print(text)